# Extracting keywords from tweets

Calculate the sentiment score of the tweets using lexicon-based models VADER and TextBlob. Both are constructed from a generalizable, valence-based, human-curated gold standard sentiment lexicon.

## Set up

In [1]:
import os
import re
import string
import pandas as pd
import numpy as np

from emot.emo_unicode import UNICODE_EMO, EMOTICONS

In [2]:
import sys
print(sys.executable)
print(sys.version)
print(sys.version_info)

/Users/alessiatosi/DS_projects/behavioural-sci-perception/venv/bin/python
3.8.1 (default, Apr  8 2020, 10:42:19) 
[Clang 11.0.0 (clang-1100.0.33.17)]
sys.version_info(major=3, minor=8, micro=1, releaselevel='final', serial=0)


In [3]:
%load_ext autoreload
from src.preproc_text import *
from src.utils import chain_functions
from src.analyse_text import get_sentiment_score_VDR, get_sentiment_score_TB

In [4]:
%reload_ext autoreload

In [5]:
os.getcwd()

'/Users/alessiatosi/DS_projects/behavioural-sci-perception/notebooks'

In [6]:
pd.options.display.max_seq_items = 10000
pd.set_option('display.max_colwidth', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.width', None)

Environment variables and constants

In [7]:
DATA_DIR = os.environ.get("DIR_DATA_INTERIM")

In [8]:
FILENAME = "tweets_original_en"

### Dictionary of keywords

In [21]:
keywords_dict = {
    "thaler" : "Actors",
    "sunstein" : "Actors",
    "kahneman" : "Actors",
    "halpern" : "Actors",
    "michie" : "Actors",
    "chater" : "Actors",
    "spi-b" : "Actors",
    "spib" : "Actors",
    "nudge unit" : "Actors",
    "nudgeunit" : "Actors",
    "behavioural insights team" : "Actors",
    "behaviouralinsightsteam" : "Actors",

    "behavioural science" : "BehavSci",
    "behavioural sciences" : "BehavSci",
    "behavioural scientist" : "BehavSci",
    "behavioural scientists" : "BehavSci",
    "behaviouralscience" : "BehavSci",
    "behaviouralsciences" : "BehavSci",
    "behaviouralscientist" : "BehavSci",
    "behaviouralscientists" : "BehavSci",

    "behavioural insight" : "Behav_ins",
    "behavioural insights": "Behav_ins",
    "behaviouralinsight" : "Behav_ins",
    "behaviouralinsights": "Behav_ins",

    "behaviour change" : "Behav_chan",
    "behavioural change" : "Behav_chan",
    "behaviourchange" : "Behav_chan",
    "behaviouralchange" : "Behav_chan",

    "behavioural policy": "Behav_pol",
    "behaviouralpolicy": "Behav_pol",

    "behavioural analysis": "Behav_anal",
    "behavioural analyst": "Behav_anal",
    "behavioural analysts": "Behav_anal",
    "behaviouralanalysis": "Behav_anal",
    "behaviouralanalyst": "Behav_anal",
    "behaviouralanalysts": "Behav_anal",

    "psychologists": "Psych",
    "psychologist": "Psych",
    "psychology": "Psych",
    "psychological science": "Psych",
    "psychological policy": "Psych",
    "psychologicalscience": "Psych",
    "psychologicalpolicy": "Psych",

    "behavioural economics": "Econ_behav",
    "behavioural economist": "Econ_behav",
    "behavioural economists": "Econ_behav",
    "behaviouraleconomics": "Econ_behav",
    "behaviouraleconomist": "Econ_behav",
    "behaviouraleconomists": "Econ_behav",

    "irrational behaviour": "Econ_irrational",
    "irrational choice": "Econ_irrational",
    "irrational choices": "Econ_irrational",
    "irrationalbehaviour": "Econ_irrational",
    "irrationalchoice": "Econ_irrational",
    "irrationalchoices": "Econ_irrational",

    "nudges": "Nudge",
    "nudge": "Nudge",
    "nudging": "Nudge",
    "nudge theory": "Nudge",
    "nudge strategy": "Nudge",
    "nudgetheory": "Nudge",
    "nudgestrategy": "Nudge",

    "choice architecture": "Nudge_choice",
    "choice architect": "Nudge_choice",
    "choicearchitecture": "Nudge_choice",
    "choicearchitect": "Nudge_choice",

    "paternalism": "Nudge_pater",
    "libertarian paternalism": "Nudge_pater",
    "libertarianpaternalism": "Nudge_pater",
    "paternalistic": "Nudge_pater",

    "pandemic": "Covid",
    "epidemic": "Covid",
    "corona": "Covid",
    "coronavirus": "Covid",
    "covid": "Covid",
    "covid-19": "Covid",
    "covid19": "Covid",
    "health emergency": "Covid",
    "healthemergency": "Covid",

    "behavioural fatigue": "Fatigue",
    "behaviouralfatigue": "Fatigue",

    "herd immunity": "Immunity",
    "herdimmunity": "Immunity"

}

## Get Data

In [9]:
tweets_df = pd.read_csv(os.path.join(DATA_DIR, FILENAME + '.csv'))

In [10]:
tweets_df.shape

(3107, 18)

# Quick glimpse

In [18]:
tweets_df.head(10)

Unnamed: 0                      created_at  \
0           5  Tue Apr 14 18:59:09 +0000 2020   
1           6  Sun Apr 19 07:41:53 +0000 2020   
2          14  Tue Apr 07 21:48:18 +0000 2020   
3          17  Sat Mar 14 19:34:45 +0000 2020   
4          26  Thu Mar 12 14:40:29 +0000 2020   
5          34  Fri May 29 23:22:25 +0000 2020   
6          35  Thu Mar 19 19:58:53 +0000 2020   
7          37  Mon May 04 12:47:08 +0000 2020   
8          39  Wed May 06 14:28:43 +0000 2020   
9          40  Thu Apr 09 20:45:48 +0000 2020   

                                                                                     hashtags  \
0                                                          NudgeUnit coronavirus HerdImmunity   
1                      rotary handwashing behaviourchange handhygieneforhealth SPATAP COVID19   
2                                                                                         NaN   
3                                                                                 coronavirus   
4                                                                                         NaN   
5                                                                                         NaN   
6                                                  behaviouralscience nudgesinthewild COVID19   
7                                                                            covid19 lockdown   
8                                                      COVID19 KomeshaCorona coronaviruskenya   
9  Winnipeg UpToSpeed Manitoba coronavirus COVID19 psychology mentalhealth behaviouralscience   

   favorite_count                   id     reweet_id retweet_screen_name lang  \
0               0  1250136530238267392           NaN                 NaN   en   
1               0  1251778026603294720           NaN                 NaN   en   
2               2  1247642382293561345           NaN                 NaN   en   
3              10  1238911465303801856           NaN                 NaN   en   
4               0  1238112632969801728           NaN                 NaN   en   
5               6  1266510234274672645           NaN                 NaN   en   
6               0  1240729478088790016  1.240444e+18        shayonislynn   en   
7               0  1257290666784235520           NaN                 NaN   en   
8               4  1258041006223765505           NaN                 NaN   en   
9               3  1248351427644325890           NaN                 NaN   en   

  place possibly_sensitive  retweet_count  \
0   NaN              False              0   
1   NaN              False              0   
2   NaN              False              0   
3   NaN              False              2   
4   NaN              False              0   
5   NaN              False              4   
6   NaN              False              4   
7   NaN              False              1   
8   NaN              False              1   
9   NaN                NaN              0   

                                                                                                                                                                                                                                                                                                     text  \
0                 "The introduction of the rules of behavior taken from the corporate sector into politics means that politicians no longer see people whom they rule as co-citizens but as employees." – @BrankoMilan …sounds familiar UK? #NudgeUnit #coronavirus #HerdImmunity https://t.co/vABII5Y2jB   
1  @chprotary 🖐️🚰 #rotary #handwashing #behaviourchange project #handhygieneforhealth WATCH VIDEO https://t.co/uKEEDPh8e0 https://t.co/HtUOzsVYKT with #SPATAP Portable Tap making communities hygienic instantly https://t.co/7X3H0SlUB7  info@handhygieneforhealth.org #COVID19 https://t.co/0PkpOJsC5Q   
2                                   "Of course, should behaviour change as governments would wish, actua

## Are there still duplicates?

Looks like there are still duplicates in the dataset that we need to get rid of. Consider re-teweet counts when doing do.

In [12]:
# Find a duplicate texts
duplicate_tweets = tweets_df[tweets_df.duplicated(['text'])]
print(duplicate_tweets[['favorite_count', 'retweet_count', 'text']])

      favorite_count  retweet_count  \
1212               0              1   
1520               0              2   
1851               1              0   
2057               0              0   
2122               0              2   
2323               2              1   
2709               0              0   
2810               1              1   
2812               1              0   
2997               0              0   

                                                                                                                                                                                                                                                                               text  
1212                                                     The deployment of behavioural science is a feature of the public health response to the Covid-19 pandemic both internationally and in Ireland, https://t.co/o16Wjg5BRd #COVID19ireland #COVID19 #nudge #behaviouralscience  
1520  "It is c

Apparently they are all duplicates of one single tweets.

We will keep the one with the largest count of "favourites". 

In [13]:
duplicate_tweets[duplicate_tweets.favorite_count == max(duplicate_tweets.favorite_count)].index

Int64Index([2323], dtype='int64')

In [14]:
# get index
duplicate_tweets_index = duplicate_tweets[duplicate_tweets.favorite_count != 
                                          max(duplicate_tweets.favorite_count)].index

In [15]:
duplicate_tweets_index

Int64Index([1212, 1520, 1851, 2057, 2122, 2709, 2810, 2812, 2997], dtype='int64')

In [16]:
tweets_df = tweets_df.drop(duplicate_tweets_index, axis=0).copy()

In [17]:
tweets_df.shape

(3098, 18)

## Extract keyword occurrences

From each tweets, we extract the keywords that appear in the tweets

#### Lower text case

In [24]:
tweets_df['text_cl'] = [t.lower() for t in tweets_df.text]

### Extract keywords

In [ ]:
# test
[[kword for kword in keywords_dict.keys() if kword in tweet] for 
 tweet in ['UK? #nudgeunit #coronavirus #herdimmunity', 'should behaviour change as governments would wish']]

In [41]:
tweets_df['subkeywords'] = [[kword for kword in keywords_dict.keys() if kword in tweet] for tweet in tweets_df.text_cl]

In [42]:
# take a look
tweets_df[['text_cl', 'subkeywords', 'favorite_count', 'retweet_count']]

text_cl  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 "the introduction of the rules of behavior taken from the corporate sector into politics means that politicians no longer see people whom they rule as co-citizens but as employees." – @brankomilan …sounds familiar uk? #nudgeunit #coronavirus #herdimmunity https://t.co/vabii5y2jb   
1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  @chprotary 🖐️🚰 #rotary #handwashing #behaviourchange project #handhygieneforhealth watch video https://t.co/ukeedph8e0 https://t.co/htuozsvykt with #spatap portable tap making communities hygienic instantly https://t.co/7x3h0slub7  info@handhygieneforhealth.org #covid19 https://t.co/0pkpojsc5q   
2                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   "of course, should behaviour change as governments would wish, actual outcomes will be less terrifying than the models had originally forecast. this is not evidence that the policy was unnecessary: rather, it is evidence that it worked." https://t.co/b5jka0d6r7   
3                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   my cartoon - he doesn’t trust doctors, he wants to see a behavioural scientist \n#coronavirus https://t.co/blcsrb88cb   
4                                                                                                                                                                                                                                

## Tweets without a keyword mentioned

These are cases where the keywords is mentioned in another tweet linked from the current tweets

### How many are they?

In [45]:
len([l for l in tweets_df.subkeywords if len(l) == 0])

462

In [48]:
no_kword_tweets_df = tweets_df[tweets_df['subkeywords'].map(lambda d: len(d)) == 0]

In [49]:
no_kword_tweets_df

Unnamed: 0                      created_at  \
5             34  Fri May 29 23:22:25 +0000 2020   
12            54  Fri Mar 20 12:20:06 +0000 2020   
26           116  Wed Apr 15 16:12:41 +0000 2020   
34           148  Mon Mar 30 10:47:19 +0000 2020   
38           159  Tue May 12 16:00:51 +0000 2020   
39           164  Sat Apr 18 13:08:19 +0000 2020   
47           174  Thu Mar 12 13:51:30 +0000 2020   
57           229  Wed Mar 18 06:59:55 +0000 2020   
58           240  Tue Mar 31 19:22:43 +0000 2020   
77           312  Tue Mar 24 23:38:27 +0000 2020   
89           366  Thu Mar 19 11:06:52 +0000 2020   
93           378  Thu Mar 12 16:42:42 +0000 2020   
96           385  Tue May 19 06:40:54 +0000 2020   
98           391  Sun Mar 22 00:09:32 +0000 2020   
101          402  Wed Apr 08 09:48:55 +0000 2020   
112          475  Thu Apr 02 06:36:56 +0000 2020   
113          477  Wed Apr 01 18:18:26 +0000 2020   
114          478  Sat Mar 21 16:17:35 +0000 2020   
127          533  Fri Mar 27 19:58:35 +0000 2020   
138          566  Tue Mar 03 22:49:40 +0000 2020   
149          597  Thu Mar 12 14:16:50 +0000 2020   
150          600  Fri May 29 09:13:19 +0000 2020   
163          654  Thu Mar 12 19:32:38 +0000 2020   
186          757  Sat Apr 04 21:26:12 +0000 2020   
189          774  Sun May 10 10:43:59 +0000 2020   
197          801  Thu Mar 12 20:45:38 +0000 2020   
198          805  Fri May 08 05:22:19 +0000 2020   
203          826  Thu May 21 12:05:58 +0000 2020   
214          855  Wed Apr 01 18:20:41 +0000 2020   
219          868  Thu Mar 26 22:29:28 +0000 2020   
224          892  Fri May 29 05:47:30 +0000 2020   
230          916  Thu May 14 11:55:38 +0000 2020   
231          917  Mon May 04 13:43:00 +0000 2020   
240          937  Sat Mar 28 01:16:40 +0000 2020   
242          940  Sun May 17 03:22:57 +0000 2020   
246          955  Sat Mar 14 08:20:47 +0000 2020   
250          970  Sat May 30 06:35:37 +0000 2020   
252          977  Fri Mar 13 11:39:40 +0000 2020   
257          999  Sat May 30 08:47:16 +0000 2020   
266         1033  Mon May 18 18:26:44 +0000 2020   
279         1073  Wed Apr 01 09:14:10 +0000 2020   
281         1082  Wed Mar 11 21:21:43 +0000 2020   
287         1107  Sat Apr 25 07:37:21 +0000 2020   
292         1119  Thu Mar 12 09:46:05 +0000 2020   
297         1135  Tue Mar 31 09:29:42 +0000 2020   
298         1146  Mon Apr 27 06:17:04 +0000 2020   
317         1238  Sun May 10 10:35:44 +0000 2020   
318         1239  Thu Mar 26 21:30:57 +0000 2020   
321         1254  Fri Mar 13 04:45:04 +0000 2020   
325         1266  Wed Mar 18 20:47:56 +0000 2020   
331         1286  Sun Apr 05 08:09:02 +0000 2020   
332         1295  Mon Mar 23 21:07:05 +0000 2020   
334         1304  Fri May 29 10:46:05 +0000 2020   
342         1327  Wed Apr 29 20:19:12 +0000 2020   
353         1354  Thu May 07 12:34:04 +0000 2020   
355         1357  Wed Mar 04 20:54:44 +0000 2020   
362         1410  Thu Mar 12 14:00:24 +0000 2020   
377         1472  Wed Mar 11 21:19:25 +0000 2020   
381         1481  Thu Mar 12 21:42:45 +0000 2020   
406         1568  Thu Jun 04 00:37:33 +0000 2020   
424         1636  Tue May 05 15:07:48 +0000 2020   
431         1676  Thu Mar 26 19:01:35 +0000 2020   
433         1680  Fri Mar 20 09:55:40 +0000 2020   
445         1717  Fri Apr 24 22:37:07 +0000 2020   
448         1730  Tue Jun 02 23:24:25 +0000 2020   
450         1734  Fri Mar 20 10:32:53 +0000 2020   
456         1774  Tue Apr 14 16:06:53 +0000 2020   
464         1799  Thu May 28 22:46:58 +0000 2020   
468         1813  Sun Mar 22 09:10:06 +0000 2020   
469         1815  Fri Mar 27 12:37:30 +0000 2020   
483         1870  Fri Mar 20 13:17:43 +0000 2020   
488         1888  Fri Apr 17 11:31:03 +0000 2020   
492         1909  Thu May 07 15:31:02 +0000 2020   
499         1928  Tue Mar 24 16:45:13 +0000 2020   
501         1934  Tue Apr 07 09:16:18 +0000 2020   
505         1947  Wed Mar 18 08:57:43 +0000 2020   
52

In [51]:
# can we quickly do it automatically?

import urllib.request
link = "https://t.co/cseXRzuw9H"


with urllib.request.urlopen(link) as url:
    s = url.read()
    # I'm guessing this would output the html source code ?
    print(s)
    
    
# too much noise

b'<!DOCTYPE html>\n<html dir="ltr" lang="en">\n<meta charset="utf-8" />\n<meta name="viewport" content="width=device-width,initial-scale=1,maximum-scale=1,user-scalable=0,viewport-fit=cover" />\n<link rel="preconnect" href="//abs.twimg.com" />\n<link rel="preconnect" href="//api.twitter.com" />\n<link rel="preconnect" href="//pbs.twimg.com" />\n<link rel="preconnect" href="//t.co" />\n<link rel="preconnect" href="//video.twimg.com" />\n<link rel="dns-prefetch" href="//abs.twimg.com" />\n<link rel="dns-prefetch" href="//api.twitter.com" />\n<link rel="dns-prefetch" href="//pbs.twimg.com" />\n<link rel="dns-prefetch" href="//t.co" />\n<link rel="dns-prefetch" href="//video.twimg.com" />\n<link rel="preload" as="script" crossorigin="anonymous" href="https://abs.twimg.com/responsive-web/client-web-legacy/polyfills.18e394f5.js" nonce="ZGY5ZjJlOWItOTQ4OC00ZTA4LWI5NWUtMDRiZTRjZjdlODI0" />\n<link rel="preload" as="script" crossorigin="anonymous" href="https://abs.twimg.com/responsive-web/clien

In [54]:
linked_tweet = "government #coronavirus science advisor dr david halpern tells me of plans to ‘cocoon’ vulnerable groups."

### Save the tweets containing no keywords

In [59]:
no_kword_tweets_df[['id', 'created_at', 'user_location', 'text_cl', 'subkeywords']].to_csv(os.path.join(DATA_DIR, "tweets_no_keywords.csv"))